Author Joshua Sudeep <br >
Summary <br> smh dude. This code generates the distance matrix? by loading texas data and open routing service api. In the end we output "gridinfosmaller.json
1. load texas data (census_tracts_2018_fips / census_tracts_2018)
2. texas data -> latitude longitude
3. latitude longitude -> distance matrix api calls


In [1]:
# unzip input file first
import xml.etree.ElementTree as ET
import requests
import math
import pprint
import time
import numpy as np
import pandas as pd
import os
import collections

### automate how big the grid is

In [84]:
# Assuming we want to make 400 squares, how should we partition the vertically/horizontally
NUM_REGIONS = 400
square_len = (vertical_distance*horizontal_distance/NUM_REGIONS)**0.5

In [80]:
# Read all census tracts and put points in dict
# CENSUS_TRACTS_DIR = "census_tracts"
CENSUS_TRACTS_DIR = "census_tracts_2018"
census_tracts_points = {} #multiple points?
census_tracts_bounding = {} #rectangle bounds?
for fname in os.listdir(CENSUS_TRACTS_DIR):
    latitudes = []
    longitudes = []
    try:
        # Parse the XML file
        root = ET.parse("{}/{}".format(CENSUS_TRACTS_DIR, fname)).getroot()
        for type_tag in root.findall("node"):
            d = type_tag.attrib
            latitudes.append(float(d["lat"]))
            longitudes.append(float(d["lon"]))
        census_tracts_points[fname.strip(".txt")] = list(zip(latitudes, longitudes))
        census_tracts_bounding[fname.strip(".txt")] = [(min(latitudes), min(longitudes)), (max(latitudes), max(longitudes))]
    except Exception as e:
        print(e)
        print(fname)
        print(list(zip(latitudes, longitudes)))

min() arg is an empty sequence
14_03.txt
[]
min() arg is an empty sequence
15_01.txt
[]
min() arg is an empty sequence
15_03.txt
[]
min() arg is an empty sequence
16_05.txt
[]
min() arg is an empty sequence
17_07.txt
[]
min() arg is an empty sequence
17_12.txt
[]
min() arg is an empty sequence
17_22.txt
[]
min() arg is an empty sequence
17_29.txt
[]
min() arg is an empty sequence
17_49.txt
[]
min() arg is an empty sequence
17_53.txt
[]
min() arg is an empty sequence
17_55.txt
[]
min() arg is an empty sequence
17_56.txt
[]
min() arg is an empty sequence
17_61.txt
[]
min() arg is an empty sequence
17_76.txt
[]
min() arg is an empty sequence
17_77.txt
[]
min() arg is an empty sequence
17_81.txt
[]
min() arg is an empty sequence
17_86.txt
[]
min() arg is an empty sequence
18_05.txt
[]
min() arg is an empty sequence
18_06.txt
[]
min() arg is an empty sequence
18_19.txt
[]
min() arg is an empty sequence
18_32.txt
[]
min() arg is an empty sequence
18_41.txt
[]
min() arg is an empty sequence
1

In [81]:
census_tracts_points

{'10': [(30.2537524, -97.7362529),
  (30.2533749, -97.7361653),
  (30.2524726, -97.7359817),
  (30.252039, -97.736191),
  (30.251999, -97.736054),
  (30.251991, -97.735916),
  (30.252018, -97.735793),
  (30.252059, -97.735753),
  (30.25211, -97.735719),
  (30.252223, -97.735705),
  (30.252413, -97.735739),
  (30.2531874, -97.7359077),
  (30.2533085, -97.7359786),
  (30.2596434, -97.736309),
  (30.2567842, -97.7236545),
  (30.2582013, -97.7365494),
  (30.2579513, -97.7358287),
  (30.2567693, -97.7340686),
  (30.2562354, -97.732529),
  (30.2560495, -97.7319932),
  (30.2564367, -97.7226793),
  (30.251725, -97.735715),
  (30.251736, -97.735572),
  (30.251771, -97.735418),
  (30.25183, -97.735298),
  (30.251915, -97.735153),
  (30.252149, -97.73493),
  (30.252258, -97.734878),
  (30.2546506, -97.7326435),
  (30.2555838, -97.7322139),
  (30.2568419, -97.7316249),
  (30.2576209, -97.7312627),
  (30.2584018, -97.7308997),
  (30.2591887, -97.730598),
  (30.2516421, -97.7149769),
  (30.2525477, 

## Travis County Boundary API

In [4]:
# root = ET.parse('input-files/RoughlyTravisCounty.osm').getroot()

In [82]:
latitudes = []
longitudes = []
# for type_tag in root.findall("node"):
#     d = type_tag.attrib
#     latitudes.append(float(d["lat"]))
#     longitudes.append(float(d["lon"]))
# min_lat_travis, max_lat_travis, min_lon_travis, max_lon_travis = float("inf"), float("-inf"), float("inf"), float("-inf")
for tract_name in census_tracts_points:
    for lat, lon in census_tracts_points[tract_name]:
#         if lat < min_lat_travis:
#             min_lat_travis = lat
#         if lon < min_lon_travis:
#             min_lon_travis = lon
#         if lat > max_lat_travis:
#             max_lat_travis = lat
#         if lon > max_lon_travis:
#             max_lon_travis = lon
        latitudes.append(lat)
        longitudes.append(lon)

## Region Mapping

In [83]:
LATITUDE_MILES = 69
LONGITUDE_MILES = 54.6

vertical_distance = (max(latitudes) - min(latitudes))*LATITUDE_MILES
horizontal_distance = (max(longitudes) - min(longitudes))*LONGITUDE_MILES

In [7]:
# Assuming we want to make 400 squares, how should we partition the vertically/horizontally
# NUM_REGIONS = 200
# square_len = (vertical_distance*horizontal_distance/NUM_REGIONS)**0.5

In [85]:
square_len

2.1323175834794137

In [87]:
latitude_delta = square_len/LATITUDE_MILES
LATITUDE_DELTA = square_len/LATITUDE_MILES
longitude_delta = square_len/LONGITUDE_MILES
LONGITUDE_DELTA = square_len/LONGITUDE_MILES
longitude_delta

0.039053435594861054

In [88]:
lat_lon = zip(latitudes, longitudes) #joins lists

In [89]:
min_lat = min(latitudes)
min_lon = min(longitudes)
max_lat = max(latitudes)
max_lon = max(longitudes)
nrows = math.ceil((max_lat - min_lat) / latitude_delta)
ncols = math.ceil((max_lon - min_lon) / longitude_delta)
def map_point_to_region(latitude, longitude):
    return math.floor((latitude-min_lat)/latitude_delta) * ncols  + math.floor((longitude-min_lon)/longitude_delta)

In [90]:
def get_representative(region_num): # 8 cols per row, # R10 --> row_num = 1, col_num = 2
    row_num = region_num//ncols # Correct
    col_num = region_num - row_num*ncols
    lat = min_lat + row_num * latitude_delta + 0.5*latitude_delta
    lon = min_lon + col_num * longitude_delta + 0.5*longitude_delta
    return [lon, lat]

In [91]:
map_point_to_region(30.084446, -97.702885)

32

In [92]:
get_representative(13)

[-97.64344371946936, 30.04071777669188]

In [93]:
valid_regions = set()
for lat, lon in zip(latitudes, longitudes):
    valid_regions.add(map_point_to_region(lat, lon))

In [94]:
valid_regions = list(valid_regions)
valid_regions.sort()

In [95]:
region_coords = [get_representative(i) for i in range(NUM_REGIONS)]

## Batch calls of distance matrix

In [96]:
# Prepare data for api call
locations = region_coords
# locations = region_coords + ems_coords + hospital_coords
durations = [[0 for i in range(200)] for j in range(NUM_REGIONS)]

In [97]:
batch_size = 1
num_batches = math.ceil(len(valid_regions) / batch_size)
num_batches_per_round = math.ceil(num_batches/4)
current_branch = 3
remainder = len(valid_regions) % batch_size
print(num_batches)

245


###  (API Key needed (https://openrouteservice.org/))

In [101]:
headers = {
    'Accept': 'application/json, application/geo+json, application/gpx+xml, img/png; charset=utf-8',
    'Authorization': '5b3ce3597851110001cf6248f4d896877baa45689a97ee0efab1d43b',
    'Content-Type': 'application/json; charset=utf-8'
}

In [102]:
# for i in range(num_batches_per_round*current_branch, min(num_batches_per_round*current_branch+num_batches_per_round, len(valid_regions))):
#     print("batch ", i)
#     start = i * batch_size
#     sources = list(range(start, start + batch_size))

#     # handle last partial batch
#     if(sources[batch_size - 1] >= len(locations)):
#         sources = sources[:remainder]

#     locations = [get_representative(valid_regions[j]) for j in range(len(valid_regions))]

#     body = {"locations": locations, "sources": sources}
#     call = requests.post('https://api.openrouteservice.org/v2/matrix/driving-car', json=body, headers=headers)

#     duration_batch = call.json()['durations']

#     for j in range(len(duration_batch)):
#         for k in range(len(duration_batch[0])):
#             durations[valid_regions[i*batch_size + j]][valid_regions[k]] = duration_batch[j][k]
#     time.sleep(0.1)


In [103]:
#ONE API CALL FOR DEBUGGING
# locations = [get_representative(i) for i in range(NUM_REGIONS)]

# durations = []
# start = 1 * 8
# sources = list(range(start, start + 8))
# body = {"locations": locations, "sources": sources}
# call = requests.post('https://api.openrouteservice.org/v2/matrix/driving-car', json=body, headers=headers)
# call.json()
# duration_batch = call.json()['durations']
# for j in range(len(duration_batch)):
#     durations.append(duration_batch[j])
# durations

In [104]:
locations = [get_representative(i) for i in range(NUM_REGIONS)]

durations = []

for i in range(25):
    start = i * 8
    sources = list(range(start, start + 8))
    body = {"locations": locations, "sources": sources}
    
    call = requests.post('https://api.openrouteservice.org/v2/matrix/driving-car', json=body, headers=headers)
    
    duration_batch = call.json()['durations']
    for j in range(len(duration_batch)):
        durations.append(duration_batch[j])
        
    time.sleep(0.1)
    
pprint.pprint(durations)


[[0.0,
  961.57,
  2006.0,
  1703.25,
  1966.77,
  2196.37,
  3745.08,
  2974.18,
  3182.53,
  3505.84,
  3856.21,
  4228.19,
  4218.59,
  4478.41,
  4731.41,
  5013.93,
  4969.52,
  5837.53,
  5408.04,
  5788.88,
  6262.38,
  2327.55,
  1870.67,
  1577.84,
  2831.08,
  2242.7,
  4065.22,
  3440.22,
  3119.99,
  3297.19,
  3887.16,
  4115.37,
  3944.35,
  4416.91,
  4423.85,
  4731.65,
  4552.82,
  4781.49,
  4919.08,
  5871.82,
  6087.55,
  5794.1,
  2606.81,
  1862.15,
  2502.87,
  2740.31,
  3125.99,
  3031.88,
  3242.97,
  3358.75,
  3465.5,
  3567.09,
  3824.27,
  4057.28,
  4281.94,
  4291.55,
  4649.02,
  5320.44,
  5100.75,
  5234.92,
  5009.83,
  5590.35,
  5361.11,
  2372.43,
  1814.96,
  2136.12,
  2480.58,
  2909.76,
  3473.54,
  4736.22,
  3775.57,
  3952.77,
  3721.83,
  4159.34,
  4280.81,
  4240.58,
  5446.79,
  4665.74,
  5009.51,
  6362.38,
  5432.94,
  5090.9,
  5396.0,
  5639.39,
  2393.84,
  2290.87,
  2180.45,
  2654.97,
  2914.52,
  2929.71,
  3643.46,
  4015.75,

  2022.22,
  2282.05,
  2535.04,
  2817.56,
  2773.16,
  3641.17,
  3211.68,
  3592.52,
  4066.02,
  3087.21,
  2128.69,
  1320.34,
  1444.14,
  437.86,
  2311.23,
  1529.06,
  923.63,
  1100.83,
  1690.79,
  1919.0,
  1747.98,
  2220.55,
  2227.49,
  2535.28,
  2356.46,
  2585.13,
  2722.72,
  3675.45,
  3891.18,
  3597.74,
  3345.59,
  1984.68,
  2211.99,
  935.47,
  1321.15,
  1447.17,
  1327.84,
  1162.39,
  1269.13,
  1370.73,
  1627.91,
  1860.92,
  2085.57,
  2095.18,
  2452.66,
  3124.07,
  2904.39,
  3038.55,
  2813.47,
  3393.99,
  3164.75,
  2136.52,
  1910.8,
  2018.54,
  910.82,
  1325.05,
  1991.99,
  2630.73,
  1680.68,
  1756.41,
  1525.46,
  1962.98,
  2084.44,
  2044.22,
  3250.42,
  2469.37,
  2813.14,
  4166.02,
  3366.45,
  3024.41,
  3199.63,
  3443.03,
  2157.93,
  1878.56,
  1378.93,
  1557.41,
  1765.01,
  1448.16,
  1937.77,
  1830.96,
  2024.39,
  1779.14,
  1885.25,
  2176.98,
  2224.08,
  2292.54,
  2397.86,
  3139.42,
  2866.34,
  3291.77,
  3455.42,
  382

  2881.81,
  3402.95,
  3637.68,
  3543.37,
  3929.22,
  4176.4,
  6066.35,
  5068.04,
  4873.9,
  5104.6,
  None,
  4664.99,
  3612.4,
  3363.49,
  2963.69,
  2974.49,
  3188.69,
  2858.95,
  2646.81,
  3052.96,
  3006.29,
  3030.16,
  3243.48,
  3381.69,
  3726.05,
  3785.2,
  4037.07,
  5596.48,
  5378.62,
  5700.38,
  5350.97,
  None,
  4079.25,
  3601.67,
  3497.93,
  3097.4,
  3062.87,
  3224.47,
  3178.5,
  2817.94,
  3115.55,
  3217.46,
  3204.35,
  3401.36,
  3354.97,
  3420.01,
  3652.16,
  3812.89,
  6172.0,
  5224.99,
  4935.91,
  5556.18,
  5065.94,
  4689.87,
  3492.99,
  3220.98,
  3060.69,
  3230.09,
  3387.91,
  3168.56,
  2985.64,
  3225.58,
  3324.93,
  3329.77,
  3365.63,
  3751.25,
  3711.49,
  3819.52,
  4088.02,
  6545.62],
 [3852.51,
  3052.86,
  2605.81,
  2149.3,
  1885.76,
  1656.15,
  1986.41,
  1078.97,
  751.42,
  459.4,
  0.0,
  511.5,
  834.75,
  1087.45,
  1340.45,
  1622.97,
  1578.56,
  2446.57,
  2017.08,
  2397.92,
  2871.42,
  4743.34,
  3784.83,
 

  1129.04,
  1050.69,
  1151.78,
  0.0,
  519.73,
  1820.48,
  1390.99,
  1771.83,
  2245.33,
  5918.97,
  4960.45,
  4152.1,
  4275.9,
  3269.62,
  3699.28,
  2917.12,
  2501.66,
  2195.37,
  2418.1,
  1828.31,
  1560.8,
  1488.97,
  1246.42,
  963.2,
  550.61,
  546.49,
  902.03,
  1854.77,
  2070.5,
  1777.05,
  6006.08,
  4761.9,
  4957.82,
  3767.22,
  4152.9,
  2926.99,
  2715.89,
  2550.44,
  2365.08,
  1854.81,
  1711.33,
  1717.83,
  1645.48,
  1158.21,
  858.65,
  1451.18,
  1083.7,
  1217.87,
  992.78,
  1573.3,
  1344.06,
  4654.33,
  4428.61,
  4536.35,
  3541.44,
  3668.33,
  4029.89,
  4018.78,
  2736.48,
  2506.04,
  2093.09,
  2122.24,
  1840.46,
  1490.23,
  2134.78,
  1148.91,
  1447.69,
  2345.33,
  1658.89,
  1229.99,
  1378.94,
  1622.34,
  4490.09,
  4396.36,
  4009.55,
  4111.89,
  3902.23,
  3211.35,
  3097.13,
  2722.69,
  2734.92,
  2235.37,
  2341.48,
  1959.79,
  1594.43,
  1619.26,
  1576.69,
  1851.33,
  1774.78,
  1836.37,
  1857.13,
  1999.64,
  2922.83

  4013.83,
  3923.27,
  4387.06,
  3973.59,
  3338.53,
  3335.83,
  3114.83,
  3014.66,
  2752.25,
  2577.07,
  2256.42,
  2188.11,
  1974.31,
  2124.03,
  2664.59,
  1900.02,
  1977.96,
  1949.02,
  4736.49,
  5004.56,
  4532.15,
  4482.95,
  4132.4,
  3795.31,
  3732.05,
  3322.05,
  3257.3,
  2906.01,
  2774.42,
  2738.01,
  2675.45,
  2439.97,
  2634.02,
  2898.91,
  3447.86,
  2320.24,
  2048.34,
  1999.91,
  2303.5,
  5008.19,
  4738.19,
  4451.71,
  4805.52,
  4677.47,
  4510.06,
  3525.59,
  3288.75,
  3486.02,
  2968.37,
  3014.35,
  2810.18,
  2801.09,
  3555.26,
  2856.44,
  3039.95,
  2894.94,
  2547.52,
  3433.38,
  2300.4,
  3457.56,
  5959.48,
  5214.51,
  4833.28,
  4634.62,
  4257.21,
  4522.25,
  3622.47,
  3697.33,
  3509.65,
  3432.27,
  3268.99,
  3069.17,
  2963.73,
  2899.66,
  2767.61,
  2586.04,
  3011.43,
  3320.1,
  2878.69,
  2742.55,
  2672.28,
  6906.55,
  6260.6,
  5218.72,
  4887.91,
  4218.41,
  4091.42,
  4149.59,
  3572.62,
  4501.2,
  3821.35,
  3356

...

  1218.57,
  1221.66,
  976.14,
  641.01,
  0.0,
  559.75,
  805.07,
  1251.34,
  1491.27,
  1577.51,
  1921.06,
  2597.57,
  2655.67,
  2748.51,
  2513.1,
  4502.65,
  3834.1,
  2792.22,
  2442.45,
  1772.95,
  1569.86,
  1616.08,
  1039.11,
  1750.73,
  946.14,
  253.4,
  628.74,
  906.91,
  1098.01,
  1282.71,
  1514.24,
  1980.27,
  2351.85,
  2112.9,
  2191.16,
  2419.1,
  3555.07,
  3473.86,
  2336.24,
  2248.57,
  1977.61,
  2058.19,
  2147.4,
  2318.56,
  1530.13,
  974.52,
  654.27,
  736.28,
  1103.26,
  1142.29,
  1473.01,
  1257.45,
  1388.33,
  1555.4,
  1697.64,
  1856.48,
  2116.38,
  4508.28,
  3372.27,
  2515.59,
  2716.65,
  3733.86,
  2304.17,
  2450.49,
  1794.96,
  1805.0,
  1021.83,
  697.46,
  740.93,
  1033.26,
  1339.45,
  1511.23,
  1662.83,
  1557.21,
  1893.64,
  1942.82,
  2198.27,
  2209.77,
  3155.64,
  2584.11,
  2782.02,
  2920.15,
  3269.59,
  3545.44,
  2485.1,
  1763.49,
  1650.6,
  1114.26,
  925.73,
  744.37,
  1097.93,
  1367.65,
  1637.32,
  1697

  1208.68,
  1634.11,
  1797.75,
  2305.78,
  3299.85,
  3278.91,
  2949.2,
  2607.75,
  2446.42,
  2355.86,
  2819.64,
  2406.18,
  1771.12,
  1768.42,
  1547.42,
  1447.24,
  1184.83,
  1006.86,
  683.87,
  801.18,
  893.74,
  1252.24,
  2102.67,
  1817.56,
  2300.86,
  2464.79,
  3169.07,
  3437.15,
  2964.73,
  2915.53,
  2564.99,
  2227.89,
  2164.63,
  1754.64,
  1689.89,
  1338.6,
  1207.01,
  1170.59,
  1108.04,
  827.22,
  766.18,
  784.37,
  2423.69,
  1371.62,
  1726.91,
  2028.33,
  2331.92,
  3440.78,
  3170.78,
  2884.3,
  3238.1,
  3110.06,
  2942.65,
  1958.18,
  1721.34,
  1918.61,
  1400.96,
  1446.94,
  1242.77,
  1179.24,
  1987.84,
  510.41,
  918.24,
  967.61,
  1071.63,
  2084.99,
  1946.67,
  2882.78,
  4392.06,
  3647.09,
  3265.86,
  3067.21,
  2689.8,
  2954.84,
  2055.06,
  2129.92,
  1942.24,
  1864.86,
  1503.14,
  1098.11,
  966.64,
  745.63,
  421.58,
  0.0,
  749.3,
  1425.81,
  1483.91,
  1959.45,
  1724.04,
  5339.14,
  4693.18,
  3651.31,
  3320.5,
 

  1469.57,
  1686.63,
  5916.69,
  5936.61,
  5513.85,
  4640.6,
  4383.37,
  4643.07,
  3601.77,
  3681.61,
  3008.75,
  2930.49,
  2865.43,
  2714.48,
  2555.08,
  2609.55,
  2527.47,
  2294.55,
  2330.52,
  2139.0,
  1978.21,
  1717.81,
  1965.0,
  6190.29,
  5191.98,
  4997.83,
  5228.54,
  None,
  4788.93,
  3736.34,
  3487.43,
  3087.62,
  3098.43,
  3150.29,
  2836.46,
  2624.32,
  2833.21,
  2419.04,
  2442.91,
  2656.23,
  2328.66,
  2160.89,
  1868.53,
  2332.57,
  5720.42,
  5502.55,
  5824.31,
  5474.91,
  None,
  4203.19,
  3725.61,
  3621.86,
  3221.33,
  3112.17,
  3151.45,
  3156.01,
  2795.46,
  2882.56,
  2630.21,
  2617.1,
  2814.11,
  2515.79,
  2265.9,
  2077.1,
  2184.4,
  6295.93,
  5348.92,
  5059.85,
  5680.12,
  5189.87,
  4813.81,
  3616.93,
  3344.92,
  3184.62,
  3354.03,
  3365.43,
  3146.07,
  2963.15,
  2992.44,
  2737.68,
  2742.51,
  2778.38,
  2905.63,
  2403.26,
  2314.72,
  2459.53,
  6669.56],
 [4762.54,
  3801.01,
  4754.1,
  4297.59,
  4034.05,
 

  2777.79,
  3549.35,
  3092.84,
  2829.3,
  2961.68,
  2638.13,
  2246.1,
  2477.63,
  2623.14,
  2829.9,
  2778.11,
  2726.17,
  3162.52,
  3415.51,
  3544.34,
  3499.94,
  4256.44,
  3826.95,
  3736.7,
  4069.01,
  4468.28,
  3445.97,
  2851.03,
  4043.82,
  2744.83,
  3115.44,
  2333.27,
  2038.04,
  2353.01,
  2654.19,
  2673.48,
  2494.27,
  2966.83,
  2850.83,
  3299.85,
  3079.68,
  3355.96,
  3337.99,
  4201.54,
  3894.17,
  3600.73,
  3899.36,
  2655.18,
  3172.66,
  2539.72,
  3109.47,
  2343.14,
  2132.04,
  1919.26,
  2460.82,
  2330.87,
  2351.36,
  2564.73,
  2628.42,
  2522.97,
  2813.51,
  3382.03,
  3210.05,
  3393.62,
  3023.51,
  3509.2,
  3167.74,
  2547.61,
  2321.9,
  2429.63,
  2158.5,
  2147.71,
  2459.67,
  3253.13,
  1850.75,
  2116.46,
  1967.66,
  2260.0,
  2380.74,
  2464.05,
  3611.27,
  2632.42,
  2808.79,
  4207.71,
  3155.44,
  2813.41,
  3131.75,
  3446.02,
  2383.37,
  2289.65,
  2024.95,
  2169.96,
  1864.65,
  1582.75,
  1818.05,
  1888.71,
  1940.

  2620.36,
  2448.39,
  2631.96,
  2261.84,
  2747.53,
  2406.07,
  2784.52,
  2558.8,
  2666.54,
  1887.04,
  1876.24,
  2148.52,
  2643.26,
  1240.88,
  1506.59,
  1205.99,
  1498.34,
  1619.08,
  1702.39,
  2849.61,
  1870.76,
  2047.13,
  3446.05,
  2393.78,
  2051.74,
  2370.08,
  2684.35,
  2620.28,
  2526.56,
  2251.99,
  2230.52,
  2032.42,
  1329.99,
  1215.76,
  1298.59,
  1350.66,
  1197.6,
  1445.63,
  1470.46,
  1466.55,
  1632.59,
  1561.41,
  2166.75,
  1893.68,
  2319.1,
  2482.75,
  2990.78,
  3984.85,
  2449.62,
  2119.91,
  1778.46,
  1617.13,
  1526.57,
  1990.35,
  1496.18,
  861.12,
  858.42,
  1004.87,
  1128.86,
  1132.99,
  1200.16,
  1247.73,
  1486.17,
  1578.74,
  1937.24,
  2787.67,
  2942.23,
  3020.17,
  3225.85,
  2339.78,
  2607.86,
  2135.44,
  2086.24,
  1735.7,
  1398.6,
  1335.34,
  925.35,
  779.89,
  692.79,
  792.78,
  1080.09,
  963.51,
  1451.45,
  1777.41,
  2042.29,
  3108.69,
  2629.54,
  2984.82,
  3042.12,
  3152.24,
  2611.49,
  2341.49,


In [105]:
len(durations[199]

SyntaxError: unexpected EOF while parsing (<ipython-input-105-0e4712d24fd0>, line 1)

In [ ]:
#This is setting the time from region i to i.
for i in range(len(durations)):
    for j in range(len(durations[0])):
        if i != j:
            continue
        durations[i][j] = 300


In [ ]:
for i in range(len(durations)):
    for j in range(len(durations[0])):
        if durations[i][j] is None:
            print(i,j)
            durations[i][j] = 300

In [ ]:
durations

In [106]:
#never used?
#def in_grid(grid_lat, grid_lon, lat, lon):
#    return (grid_lat <= lat <= grid_lat + LATITUDE_DELTA and grid_lon <= lon <= grid_lon + LONGITUDE_DELTA)

In [107]:
census_tract_grids = collections.defaultdict(set)
visited = set()
for tract_name in census_tracts_points:
    for lat, lon in census_tracts_points[tract_name]:
        region = map_point_to_region(lat, lon)
#         if region not in visited:
        census_tract_grids[tract_name].add(region)
#         visited.add(region)
    census_tract_grids[tract_name] = list(census_tract_grids[tract_name])

### This is where we export the json

In [113]:
import json

d = {"latitude_min": min_lat, "longitude_min": min_lon, "latitude_max": max_lat, "longitude_max": max_lon, "latitude_step": latitude_delta, "longitude_step": longitude_delta}
d["time_matrix"] = durations
d["census_tract_region_mapping"] = dict(census_tract_grids)
d["NUM_REGIONS"] = NUM_REGIONS
# with open("grid_info_multiple.json", "w") as j:
s = "grid_info_" + str(NUM_REGIONS) + ".json"
s

'grid_info_400.json'

In [114]:
with open(s, "w") as j:
    json.dump(d, j)

In [6]:
import json
with open("../austin-ems-data/grid_info_multiple.json", "r") as j:
    info = json.load(j)

In [7]:
info["time_matrix"]

dict_keys(['latitude_min', 'longitude_min', 'latitude_max', 'longitude_max', 'latitude_step', 'longitude_step', 'time_matrix', 'census_tract_region_mapping'])